In [217]:
import colorcet
import numpy as np
import os
import pandas as pd
import tensorflow as tf
import time

from bokeh.io import output_notebook, export_png, output_file, reset_output
from bokeh.layouts import row, column
from bokeh.palettes import linear_palette
from bokeh.plotting import figure, output_file, show, ColumnDataSource
from bokeh.models import Range1d, HoverTool, CustomJS, Slider, ColorBar, LinearColorMapper, CategoricalColorMapper, Arrow, VeeHead, GlyphRenderer
from copy import copy

reset_output()
output_notebook()

os.environ["KMP_DUPLICATE_LIB_OK"]="TRUE"

Loading BokehJS ...

In [2]:
def l2_loss(pred, y):
    return (y - pred) ** 2
l2_loss = np.vectorize(l2_loss)

In [44]:
def gradient(x, w, y):
    tx = tf.Variable(initial_value=x)
    tw = tf.Variable(initial_value=w)
    ty = tf.Variable(initial_value=y)
    with tf.GradientTape() as tape:
        loss = tf.sqrt(tf.reduce_mean((ty - tf.matmul(tx, tw)) ** 2))
    
    loss_grad = tape.gradient(loss, tw)
    return loss, loss_grad.numpy()

In [96]:
n = 300
x = np.array([np.random.normal(0, 0.5, n), np.random.normal(1.25, 0.5, n)]).T
y = np.matmul(x, np.array([1.56, -1.62]).T)

w0, w1 = np.meshgrid(np.linspace(-50., 50., num=400), np.linspace(-50., 50., num=400))
w = np.array([w0.ravel(), w1.ravel()])

loss = np.sqrt(np.average(((y.reshape(n, 1) - np.matmul(x, w)) ** 2), axis=0))

In [174]:
color_mapper = LinearColorMapper(linear_palette(colorcet.bmy, 256), low=np.min(loss), high=np.max(loss))
color_bar = ColorBar(color_mapper=color_mapper, border_line_color=None, location=(0,0))
plots = []
for eta, num_it in zip([3, 5, 20], [30, 20, 7]):
    p = figure(title=f'Root Mean Square Error (η={eta}, it={num_it})', tooltips=[('w1', '$x'), ('w2', '$y'), ('loss', '@image')], tools=['pan', 'wheel_zoom', 'reset', 'save'], x_axis_label='w1', y_axis_label='w2')
    p.image(image=[loss.reshape(400, 400)], x=-50, y=-50, dw=100, dh=100, color_mapper=color_mapper)
    p.x_range.range_padding = p.y_range.range_padding = 0
    p.add_layout(color_bar, 'right')
    p.title.align = 'center'
    p.title.text_font_size = p.xaxis.axis_label_text_font_size = p.yaxis.axis_label_text_font_size = "16pt"

    pos = np.array([-40., -40.]).reshape(2, 1)
    iterations = np.arange(num_it)
    size = 15 - iterations
    size[size < 5] = 5
    for it in iterations:
        p.circle(x=pos[0, 0], y=pos[1, 0], line_color='#ffffff', size=5, color='#ffffff')

        l, l_grad = gradient(x, pos, y)
        p.add_layout(Arrow(end=VeeHead(line_color='#ffffff', fill_color='#ffffff', size=size[it]), line_color='#ffffff',
                           line_width=2, x_start=pos[0, 0], y_start=pos[1, 0], x_end=pos[0, 0] - eta * l_grad[0, 0], y_end=pos[1, 0] - eta * l_grad[1, 0]))
        pos[0, 0] -= eta * l_grad[0, 0]
        pos[1, 0] -= eta * l_grad[1, 0]
    plots.append(p)

show(plots[0])
show(plots[1])
show(plots[2])
_ = export_png(plots[0], filename='Learning Rate (1).png')
_ = export_png(plots[1], filename='Learning Rate (2).png')
_ = export_png(plots[2], filename='Learning Rate (3).png')